In [32]:
#!pip install huggingface_hub torch transformers datasets trl 
#!pip install flash-attn --no-build-isolation
!pip install --upgrade peft

In [2]:
import sys
import logging

import datasets
from datasets import load_dataset
from peft import LoraConfig
import torch
import transformers
from trl import SFTTrainer, SFTConfig
from transformers import AutoModelForCausalLM, AutoTokenizer, TrainingArguments, BitsAndBytesConfig

In [3]:
dataset_id = ("wikitext", "wikitext-103-raw-v1")
dataset_id = "HuggingFaceH4/ultrachat_200k"

dataset = load_dataset(dataset_id)

In [4]:
training_config = {
    "bf16": True,
    "do_eval": False,
    "do_train": True, # defualts to False, not sure where this fits
    "learning_rate": 5.0e-06,
    "log_level": "info",
    "logging_steps": 20,
    "logging_strategy": "steps",
    "lr_scheduler_type": "cosine",
    "num_train_epochs": 1,
    "max_steps": -1,
    "output_dir": "./checkpoint_dir", # model predictions and checkpoints
    "overwrite_output_dir": True,
    "per_device_eval_batch_size": 4,
    "per_device_train_batch_size": 4,
    "remove_unused_columns": True,
    "save_steps": 100,
    "save_total_limit": 1,
    "seed": 0,
    "gradient_checkpointing": True,
    "gradient_checkpointing_kwargs":{"use_reentrant": False},
    "gradient_accumulation_steps": 1, # number of steps to accumulate before beckprop
    "warmup_ratio": 0.2,
    "packing": False,
    "max_seq_length": 2048,
    "dataset_text_field": "text",
    }

peft_config = {
    "r": 16, # default values VV
    "lora_alpha": 32,
    "lora_dropout": 0.05,
    "bias": "none",
    "task_type": "CAUSAL_LM",
    "target_modules": "all-linear",
    "modules_to_save": None,
}

train_conf = SFTConfig(**training_config)
#train_conf = TrainingArguments(**training_config)
peft_conf = LoraConfig(**peft_config)

In [ ]:
checkpoint_path = "microsoft/Phi-3-mini-128k-instruct"
model_kwargs = dict(
    use_cache=False,
    trust_remote_code=True,
    attn_implementation="flash_attention_2",  # loading the model with flash-attenstion support
    torch_dtype=torch.bfloat16,
    device_map="auto"
)

model = AutoModelForCausalLM.from_pretrained(checkpoint_path, **model_kwargs)
tokenizer = AutoTokenizer.from_pretrained(checkpoint_path, truncation=True)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Exception ignored in: <bound method IPythonKernel._clean_thread_parent_frames of <ipykernel.ipkernel.IPythonKernel object at 0x76c288d725c0>>
Traceback (most recent call last):
  File "/opt/conda/lib/python3.10/site-packages/ipykernel/ipkernel.py", line 775, in _clean_thread_parent_frames
    def _clean_thread_parent_frames(
KeyboardInterrupt: 
Exception ignored in: <bound method IPythonKernel._clean_thread_parent_frames of <ipykernel.ipkernel.IPythonKernel object at 0x76c288d725c0>>
Traceback (most recent call last):
  File "/opt/conda/lib/python3.10/site-packages/ipykernel/ipkernel.py", line 775, in _clean_thread_parent_frames
    def _clean_thread_parent_frames(
KeyboardInterrupt: 
Exception ignored in: <bound method IPythonKernel._clean_thread_parent_frames of <ipykernel.ipkernel.IPythonKernel object at 0x76c288d725c0>>
Traceback (most recent call last):
  File "/opt/conda/lib/python3.10/site-packages/ipykernel/ipkernel.py", line 775, in _clean_thread_parent_frames
    def _clean_t

In [6]:
tokenizer.model_max_length = 2048
#tokenizer.pad_token = tokenizer.unk_token  # use unk rather than eos token to prevent endless generation
#tokenizer.pad_token_id = tokenizer.convert_tokens_to_ids(tokenizer.pad_token)
tokenizer.padding_side = 'right'

In [7]:
def preproc(examples, tokenizer):
    messages = examples['messages']
    examples['text'] = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=False) #, return_dict=True)
    return examples

train_dataset = dataset['train_sft']
test_dataset = dataset['test_sft']

train_dataset = train_dataset.map(preproc,
                            fn_kwargs={'tokenizer':tokenizer},
                            num_proc=24,
                            #batched=True,
                            remove_columns=list(train_dataset.features)).select(range(1000))

test_dataset = test_dataset.map(preproc,
                            fn_kwargs={'tokenizer':tokenizer},
                            num_proc=24,
                            #batched=True,
                            remove_columns=list(test_dataset.features))#[10000:]

In [8]:
trainer = SFTTrainer(
    model=model,
    args=train_conf,
    peft_config=peft_conf,
    train_dataset=train_dataset,
    #eval_dataset=test_dataset,
    # max_seq_length=tokenizer.model_max_length,
    # dataset_text_field="text",
    tokenizer=tokenizer,
    # packing=True
)

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

Using auto half precision backend


In [16]:
train_result = trainer.train()
metrics = train_result.metrics
trainer.save_state()

***** Running training *****
  Num examples = 1,000
  Num Epochs = 1
  Instantaneous batch size per device = 4
  Total train batch size (w. parallel, distributed & accumulation) = 4
  Gradient Accumulation steps = 1
  Total optimization steps = 250
  Number of trainable parameters = 25,165,824


KeyboardInterrupt: 

In [12]:
metrics

{'train_runtime': 506.2204,
 'train_samples_per_second': 1.975,
 'train_steps_per_second': 0.494,
 'total_flos': 4.041582948790272e+16,
 'train_loss': 1.1037534561157227,
 'epoch': 1.0}

In [ ]:
from peft import PeftConfig, PeftModel 

checkpoint_path = "microsoft/Phi-3-mini-128k-instruct"
adapter_path = "./checkpoint_dir/checkpoint-250"

model_kwargs = dict(
    use_cache=False,
    trust_remote_code=True,
    attn_implementation="flash_attention_2",  # loading the model with flash-attenstion support
    torch_dtype=torch.bfloat16,
    device_map="auto"
)

model = AutoModelForCausalLM.from_pretrained(checkpoint_path, **model_kwargs)

In [8]:
model = PeftModel.from_pretrained(model, adapter_path)
tokenizer = AutoTokenizer.from_pretrained(checkpoint_path)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [22]:
input_text = [
    {'role': 'user', 'content': "Tell me about cats"},
]

input = "Tell me about cats"

input = tokenizer(input, return_tensors='pt')

output = model.generate(
    input['input_ids'].to('cuda'),
    max_length=50,  # Maximum length of the generated text
    num_return_sequences=1,  # Number of sequences to generate
)

In [23]:
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print(generated_text)

Tell me about cats.

Chatbot: Cats are fascinating creatures! They are known for their agility, independence, and unique behaviors. They have a keen sense of hearing and can see well in low light
